In [1]:
import sys
sys.path.append('/SEE-MTDA/see')
from sc.mesher.mesher import Mesher
import numpy as np
import os
import glob
from pathlib import Path
from sc.datasets.shared_utils import *
import open3d as o3d
from easydict import EasyDict
import yaml

def cfg_from_yaml_file(cfg_file):
    cfg = EasyDict()
    print("\n----- Cfgs -----")
    with open(cfg_file, 'r') as f:
        yaml_config = yaml.safe_load(f)
        print(yaml.dump(yaml_config))

    cfg.update(EasyDict(yaml_config))

    return cfg

cfg_file = '/SEE-MTDA/see/sc/cfgs/KIT-DM-ORH005.yaml'
cfg = cfg_from_yaml_file(cfg_file)
mesher = Mesher(cfg=cfg, cfg_path=cfg_file)

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.

----- Cfgs -----
DATASET:
  CAMERA_CHANNELS:
  - image_2
  CLASSES:
  - Car
  DET2D_MASK: true
  DET2D_MODEL: htc
  NAME: kitti
  POINT_CLOUD_RANGE:
  - -70
  - -70
  - -2
  - 70
  - 70
  - 4
  SHRINK_MASK_PERCENTAGE: 2
DATA_PATH: /SEE-MTDA/data/kitti
MESHER:
  CLUSTERING:
    EPS_SCALING: 5
    NAME: db_scan
  MESH_ALGORITHM:
    LOWER_RADIUS: 0.01
    NAME: ball_pivoting
    UPPER_RADIUS: 1.155
  MIN_LIDAR_PTS_TO_MESH: 30
  NAME: det_mesh
  REPLACE_OBJECT_WITH_MESH:
    POINT_DISTANCE_THRESH: 0.1
  SAMPLING:
    NAME: vres_ring_based_sampling
    OPTIMAL_RING_HEIGHT: 0.05
    TYPE: poisson
  VRES: 0.4

Loading masks...
loading annotations into memory...
Done (t=0.98s)
creating index...
index created!
KittiObjects initialised!

Mesher Initialised!


# Export points in GT box

This is to assess shape completion with perfect data

In [2]:
mesher.min_lidar_pts_to_mesh = 5

for sample_idx in range(mesher.data_obj.__len__()):
    pcd_gtboxes = mesher.get_pcd_gtboxes(sample_idx)

    for object_id in range(len(pcd_gtboxes['gt_boxes'])):    

        object_pcd = pcd_gtboxes['pcd'].crop(pcd_gtboxes['gt_boxes'][object_id])

        if len(object_pcd.points) < mesher.min_lidar_pts_to_mesh:
            continue

        box_pts = np.asarray(pcd_gtboxes['gt_boxes'][object_id].get_box_points())

        if mesher.data_obj.dataset_name == 'nuscenes':
            fname = f'nsweeps-{mesher.data_obj.nsweeps}_frame-{sample_idx}_object-{object_id}_car_pts-{len(object_pcd.points)}'
        else:
            fname = f'frame-{sample_idx}_object-{object_id}_car_pts-{len(object_pcd.points)}'

        car_dir = Path(f'{mesher.data_obj.root_dir}/exported/cars')
        car_dir.mkdir(parents=True, exist_ok=True)
        o3d.io.write_point_cloud(str(car_dir / f'{fname}.pcd'), object_pcd)

        box_dir = Path(f'{mesher.data_obj.root_dir}/exported/bboxes')    
        box_dir.mkdir(parents=True, exist_ok=True)
        np.savetxt(str(box_dir / f'{fname}.txt'), box_pts, delimiter=' ')

        print(f"frame-{sample_idx}: Exported {object_id}/{len(pcd_gtboxes['gt_boxes'])} | car_pts-{len(object_pcd.points)}")


frame-1: Exported 0/1 | car_pts-9
frame-2: Exported 0/1 | car_pts-53


KeyboardInterrupt: 

# Export points in mask/bbox

This is to test out lidar segmentation on the points within a box

In [2]:
from PIL import Image

export_tag = 'bbox'
if export_tag == 'bbox':
    use_bbox = True
else:
    use_bbox = False

instance_dataset_id = 0
for sample_idx in range(mesher.data_obj.__len__()):
    
    i_clouds = mesher.data_obj.get_mask_instance_clouds(sample_idx, append_labels=False, use_bbox=use_bbox)
    pcd_gtboxes = mesher.get_pcd_gtboxes(sample_idx, add_ground_lift=False)    
    inst_labels = mesher.data_obj.get_camera_instances(sample_idx, channel='image_2')
        
    for object_id, i_cloud in enumerate(i_clouds):
        mask_pcd = convert_to_o3dpcd(i_clouds[object_id])
        cropped_pcds, num_pts_in_gt_for_mask = [], []        
        
        if len(i_cloud) < 5:
            continue
            
        for i in range(len(pcd_gtboxes['gt_boxes'])):    
            cropped = mask_pcd.crop(pcd_gtboxes['gt_boxes'][i])
            num_pts_in_gt_for_mask.append(len(cropped.points))
            cropped_pcds.append(cropped)            
            
        if not num_pts_in_gt_for_mask or max(num_pts_in_gt_for_mask) == 0:
            labelled_pts = np.hstack([i_cloud[:,:3], np.zeros((len(i_cloud),1))])
            box_pts = np.zeros((8,3))
            num_points_in_gt = 0
        else:
            gtbox_idx = np.argmax(np.array(num_pts_in_gt_for_mask)) 
            
            cropped_np = np.array(cropped_pcds[gtbox_idx].points)
            obj_pts_labelled = np.hstack([cropped_np, 10*np.ones((len(cropped_np),1))])

            dist = mask_pcd.compute_point_cloud_distance(cropped_pcds[gtbox_idx])
            cropped_inds = np.where(np.asarray(dist) < 0.01)[0]
            mask_without_obj = np.asarray(mask_pcd.select_by_index(cropped_inds, invert=True).points)
            mask_pts_labelled = np.hstack([mask_without_obj, np.zeros((len(mask_without_obj),1))])

            labelled_pts = np.vstack([mask_pts_labelled, obj_pts_labelled])
            box_pts = np.asarray(pcd_gtboxes['gt_boxes'][gtbox_idx].get_box_points())
            num_points_in_gt = len(cropped_np)
               
        # Save pcl
        fname = f"{instance_dataset_id:06}"
        car_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/velodyne')
        car_dir.mkdir(parents=True, exist_ok=True)
        car_fname = str(car_dir / f'{fname}.bin')
        points = np.float32(labelled_pts)
        points.tofile(car_fname)
        
        # Save points labels
        label_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/labels')
        label_dir.mkdir(parents=True, exist_ok=True)
        label_fname = str(label_dir / f'{fname}.label')
        labels = np.uint32(labelled_pts[:,3])
        labels.tofile(label_fname)
        
        # Save gt bboxes
        box_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/gt_bboxes')    
        box_dir.mkdir(parents=True, exist_ok=True)
        np.savetxt(str(box_dir / f'{fname}.txt'), box_pts, delimiter=' ')
        
        # Save img
        img_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/image')    
        img_dir.mkdir(parents=True, exist_ok=True)
        img = mesher.data_obj.get_image(sample_idx, channel="image_2")
        imglabels = inst_labels[object_id]
        ann_img = draw_lidar_on_image([], img, instances=[imglabels], display=False)
        Image.fromarray(ann_img).save(str(img_dir / f'{fname}.png'))

        print(f"car #{instance_dataset_id}: Exported {object_id+1}/{len(i_clouds)} | total pts-{len(labelled_pts)}, gt pts - {num_points_in_gt}")
        instance_dataset_id = instance_dataset_id + 1

car #0: Exported 1/1 | total pts-10, gt pts - 9
car #1: Exported 1/1 | total pts-110, gt pts - 67
car #2: Exported 1/4 | total pts-408, gt pts - 0
car #3: Exported 2/4 | total pts-952, gt pts - 674
car #4: Exported 4/4 | total pts-15, gt pts - 0
car #5: Exported 1/3 | total pts-120, gt pts - 68
car #6: Exported 2/3 | total pts-33, gt pts - 25
car #7: Exported 1/5 | total pts-666, gt pts - 321
car #8: Exported 2/5 | total pts-138, gt pts - 65
car #9: Exported 3/5 | total pts-98, gt pts - 26
car #10: Exported 4/5 | total pts-10, gt pts - 0
car #11: Exported 5/5 | total pts-16, gt pts - 0
car #12: Exported 1/3 | total pts-213, gt pts - 182
car #13: Exported 2/3 | total pts-25, gt pts - 20
car #14: Exported 3/3 | total pts-7, gt pts - 5
car #15: Exported 1/10 | total pts-2959, gt pts - 1371
car #16: Exported 2/10 | total pts-1579, gt pts - 860
car #17: Exported 3/10 | total pts-3099, gt pts - 1627
car #18: Exported 4/10 | total pts-1038, gt pts - 658
car #19: Exported 5/10 | total pts-298,

car #160: Exported 2/7 | total pts-345, gt pts - 173
car #161: Exported 3/7 | total pts-113, gt pts - 62
car #162: Exported 4/7 | total pts-102, gt pts - 30
car #163: Exported 5/7 | total pts-44, gt pts - 20
car #164: Exported 6/7 | total pts-25, gt pts - 20
car #165: Exported 7/7 | total pts-10, gt pts - 0
car #166: Exported 1/6 | total pts-3209, gt pts - 1938
car #167: Exported 2/6 | total pts-640, gt pts - 429
car #168: Exported 3/6 | total pts-128, gt pts - 113
car #169: Exported 4/6 | total pts-136, gt pts - 106
car #170: Exported 5/6 | total pts-55, gt pts - 21
car #171: Exported 6/6 | total pts-49, gt pts - 26
car #172: Exported 1/9 | total pts-1543, gt pts - 996
car #173: Exported 2/9 | total pts-527, gt pts - 291
car #174: Exported 3/9 | total pts-190, gt pts - 156
car #175: Exported 4/9 | total pts-138, gt pts - 30
car #176: Exported 5/9 | total pts-169, gt pts - 153
car #177: Exported 6/9 | total pts-153, gt pts - 100
car #178: Exported 7/9 | total pts-25, gt pts - 12
car #1

car #318: Exported 1/8 | total pts-1433, gt pts - 223
car #319: Exported 2/8 | total pts-1854, gt pts - 60
car #320: Exported 3/8 | total pts-1318, gt pts - 448
car #321: Exported 4/8 | total pts-201, gt pts - 60
car #322: Exported 5/8 | total pts-216, gt pts - 59
car #323: Exported 6/8 | total pts-77, gt pts - 38
car #324: Exported 7/8 | total pts-48, gt pts - 8
car #325: Exported 8/8 | total pts-31, gt pts - 0
car #326: Exported 1/2 | total pts-156, gt pts - 123
car #327: Exported 2/2 | total pts-14, gt pts - 2
car #328: Exported 1/7 | total pts-1646, gt pts - 727
car #329: Exported 2/7 | total pts-156, gt pts - 48
car #330: Exported 3/7 | total pts-476, gt pts - 347
car #331: Exported 4/7 | total pts-451, gt pts - 189
car #332: Exported 5/7 | total pts-357, gt pts - 182
car #333: Exported 6/7 | total pts-184, gt pts - 76
car #334: Exported 7/7 | total pts-97, gt pts - 25
car #335: Exported 1/6 | total pts-844, gt pts - 485
car #336: Exported 2/6 | total pts-77, gt pts - 58
car #337:

car #475: Exported 4/11 | total pts-380, gt pts - 91
car #476: Exported 5/11 | total pts-647, gt pts - 314
car #477: Exported 6/11 | total pts-400, gt pts - 191
car #478: Exported 7/11 | total pts-179, gt pts - 66
car #479: Exported 8/11 | total pts-328, gt pts - 134
car #480: Exported 9/11 | total pts-179, gt pts - 101
car #481: Exported 10/11 | total pts-87, gt pts - 46
car #482: Exported 11/11 | total pts-57, gt pts - 11
car #483: Exported 1/8 | total pts-3045, gt pts - 1879
car #484: Exported 2/8 | total pts-472, gt pts - 319
car #485: Exported 3/8 | total pts-367, gt pts - 191
car #486: Exported 4/8 | total pts-219, gt pts - 155
car #487: Exported 5/8 | total pts-153, gt pts - 101
car #488: Exported 6/8 | total pts-176, gt pts - 82
car #489: Exported 7/8 | total pts-116, gt pts - 69
car #490: Exported 8/8 | total pts-68, gt pts - 39
car #491: Exported 1/11 | total pts-518, gt pts - 354
car #492: Exported 2/11 | total pts-190, gt pts - 0
car #493: Exported 3/11 | total pts-439, gt 

car #633: Exported 2/4 | total pts-429, gt pts - 226
car #634: Exported 3/4 | total pts-160, gt pts - 84
car #635: Exported 4/4 | total pts-105, gt pts - 30
car #636: Exported 1/1 | total pts-888, gt pts - 561
car #637: Exported 1/10 | total pts-2860, gt pts - 1947
car #638: Exported 2/10 | total pts-1431, gt pts - 529
car #639: Exported 3/10 | total pts-1277, gt pts - 706
car #640: Exported 4/10 | total pts-774, gt pts - 421
car #641: Exported 5/10 | total pts-580, gt pts - 169
car #642: Exported 6/10 | total pts-503, gt pts - 337
car #643: Exported 7/10 | total pts-491, gt pts - 274
car #644: Exported 8/10 | total pts-212, gt pts - 145
car #645: Exported 9/10 | total pts-51, gt pts - 35
car #646: Exported 10/10 | total pts-83, gt pts - 40
car #647: Exported 1/6 | total pts-130, gt pts - 11
car #648: Exported 2/6 | total pts-41, gt pts - 14
car #649: Exported 3/6 | total pts-40, gt pts - 28
car #650: Exported 1/3 | total pts-1348, gt pts - 262
car #651: Exported 2/3 | total pts-2139, 

...

car #35179: Exported 2/6 | total pts-1910, gt pts - 1000
car #35180: Exported 3/6 | total pts-509, gt pts - 169
car #35181: Exported 4/6 | total pts-463, gt pts - 249
car #35182: Exported 5/6 | total pts-297, gt pts - 35
car #35183: Exported 6/6 | total pts-302, gt pts - 165
car #35184: Exported 1/1 | total pts-43, gt pts - 26
car #35185: Exported 1/1 | total pts-404, gt pts - 274
car #35186: Exported 1/4 | total pts-209, gt pts - 156
car #35187: Exported 2/4 | total pts-46, gt pts - 40
car #35188: Exported 3/4 | total pts-27, gt pts - 6
car #35189: Exported 4/4 | total pts-17, gt pts - 1
car #35190: Exported 1/1 | total pts-11, gt pts - 6
car #35191: Exported 1/2 | total pts-532, gt pts - 296
car #35192: Exported 2/2 | total pts-53, gt pts - 34
car #35193: Exported 1/7 | total pts-2294, gt pts - 583
car #35194: Exported 2/7 | total pts-400, gt pts - 253
car #35195: Exported 3/7 | total pts-144, gt pts - 67
car #35196: Exported 4/7 | total pts-171, gt pts - 108
car #35197: Exported 5/7

car #35331: Exported 2/4 | total pts-65, gt pts - 33
car #35332: Exported 3/4 | total pts-66, gt pts - 16
car #35333: Exported 4/4 | total pts-23, gt pts - 11
car #35334: Exported 1/9 | total pts-1138, gt pts - 559
car #35335: Exported 2/9 | total pts-530, gt pts - 344
car #35336: Exported 3/9 | total pts-303, gt pts - 213
car #35337: Exported 4/9 | total pts-218, gt pts - 171
car #35338: Exported 5/9 | total pts-97, gt pts - 48
car #35339: Exported 6/9 | total pts-121, gt pts - 17
car #35340: Exported 7/9 | total pts-77, gt pts - 52
car #35341: Exported 8/9 | total pts-34, gt pts - 24
car #35342: Exported 9/9 | total pts-27, gt pts - 6
car #35343: Exported 1/7 | total pts-125, gt pts - 65
car #35344: Exported 2/7 | total pts-132, gt pts - 41
car #35345: Exported 3/7 | total pts-150, gt pts - 129
car #35346: Exported 4/7 | total pts-114, gt pts - 87
car #35347: Exported 5/7 | total pts-48, gt pts - 14
car #35348: Exported 7/7 | total pts-18, gt pts - 10
car #35349: Exported 1/8 | total

car #35483: Exported 3/7 | total pts-243, gt pts - 149
car #35484: Exported 4/7 | total pts-46, gt pts - 30
car #35485: Exported 5/7 | total pts-7, gt pts - 0
car #35486: Exported 6/7 | total pts-16, gt pts - 9
car #35487: Exported 1/6 | total pts-653, gt pts - 402
car #35488: Exported 2/6 | total pts-13, gt pts - 0
car #35489: Exported 3/6 | total pts-9, gt pts - 0
car #35490: Exported 1/12 | total pts-1323, gt pts - 921
car #35491: Exported 2/12 | total pts-650, gt pts - 323
car #35492: Exported 3/12 | total pts-480, gt pts - 205
car #35493: Exported 4/12 | total pts-222, gt pts - 127
car #35494: Exported 5/12 | total pts-103, gt pts - 0
car #35495: Exported 6/12 | total pts-59, gt pts - 13
car #35496: Exported 7/12 | total pts-101, gt pts - 26
car #35497: Exported 8/12 | total pts-52, gt pts - 0
car #35498: Exported 9/12 | total pts-117, gt pts - 59
car #35499: Exported 10/12 | total pts-40, gt pts - 0
car #35500: Exported 11/12 | total pts-35, gt pts - 0
car #35501: Exported 12/12 

car #35634: Exported 2/5 | total pts-36, gt pts - 0
car #35635: Exported 3/5 | total pts-50, gt pts - 7
car #35636: Exported 4/5 | total pts-26, gt pts - 24
car #35637: Exported 5/5 | total pts-9, gt pts - 0
car #35638: Exported 1/6 | total pts-167, gt pts - 59
car #35639: Exported 2/6 | total pts-226, gt pts - 128
car #35640: Exported 3/6 | total pts-97, gt pts - 28
car #35641: Exported 4/6 | total pts-43, gt pts - 24
car #35642: Exported 5/6 | total pts-13, gt pts - 0
car #35643: Exported 6/6 | total pts-15, gt pts - 0
car #35644: Exported 1/4 | total pts-57, gt pts - 29
car #35645: Exported 2/4 | total pts-119, gt pts - 52
car #35646: Exported 3/4 | total pts-40, gt pts - 14
car #35647: Exported 4/4 | total pts-21, gt pts - 14
car #35648: Exported 1/4 | total pts-139, gt pts - 95
car #35649: Exported 2/4 | total pts-81, gt pts - 48
car #35650: Exported 3/4 | total pts-38, gt pts - 17
car #35651: Exported 1/10 | total pts-1178, gt pts - 237
car #35652: Exported 2/10 | total pts-1950,

car #35786: Exported 14/16 | total pts-223, gt pts - 118
car #35787: Exported 15/16 | total pts-68, gt pts - 49
car #35788: Exported 16/16 | total pts-90, gt pts - 24
car #35789: Exported 1/7 | total pts-885, gt pts - 210
car #35790: Exported 2/7 | total pts-1245, gt pts - 910
car #35791: Exported 3/7 | total pts-571, gt pts - 331
car #35792: Exported 4/7 | total pts-161, gt pts - 66
car #35793: Exported 5/7 | total pts-102, gt pts - 66
car #35794: Exported 6/7 | total pts-25, gt pts - 0
car #35795: Exported 7/7 | total pts-34, gt pts - 4
car #35796: Exported 1/2 | total pts-2275, gt pts - 823
car #35797: Exported 2/2 | total pts-15, gt pts - 0
car #35798: Exported 1/1 | total pts-1431, gt pts - 941
car #35799: Exported 1/12 | total pts-1322, gt pts - 25
car #35800: Exported 2/12 | total pts-1811, gt pts - 776
car #35801: Exported 3/12 | total pts-812, gt pts - 459
car #35802: Exported 4/12 | total pts-202, gt pts - 111
car #35803: Exported 5/12 | total pts-256, gt pts - 138
car #35804

In [3]:
from PIL import Image

export_tag = 'mask'
if export_tag == 'bbox':
    use_bbox = True
else:
    use_bbox = False

instance_dataset_id = 0
for sample_idx in range(mesher.data_obj.__len__()):
    
    i_clouds = mesher.data_obj.get_mask_instance_clouds(sample_idx, append_labels=False, use_bbox=use_bbox)
    pcd_gtboxes = mesher.get_pcd_gtboxes(sample_idx, add_ground_lift=False)    
    inst_labels = mesher.data_obj.get_camera_instances(sample_idx, channel='image_2')
        
    for object_id, i_cloud in enumerate(i_clouds):
        mask_pcd = convert_to_o3dpcd(i_clouds[object_id])
        cropped_pcds, num_pts_in_gt_for_mask = [], []        
        
        if len(i_cloud) < 5:
            continue
            
        for i in range(len(pcd_gtboxes['gt_boxes'])):    
            cropped = mask_pcd.crop(pcd_gtboxes['gt_boxes'][i])
            num_pts_in_gt_for_mask.append(len(cropped.points))
            cropped_pcds.append(cropped)            
            
        if not num_pts_in_gt_for_mask or max(num_pts_in_gt_for_mask) == 0:
            labelled_pts = np.hstack([i_cloud[:,:3], np.zeros((len(i_cloud),1))])
            box_pts = np.zeros((8,3))
            num_points_in_gt = 0
        else:
            gtbox_idx = np.argmax(np.array(num_pts_in_gt_for_mask)) 
            
            cropped_np = np.array(cropped_pcds[gtbox_idx].points)
            obj_pts_labelled = np.hstack([cropped_np, 10*np.ones((len(cropped_np),1))])

            dist = mask_pcd.compute_point_cloud_distance(cropped_pcds[gtbox_idx])
            cropped_inds = np.where(np.asarray(dist) < 0.01)[0]
            mask_without_obj = np.asarray(mask_pcd.select_by_index(cropped_inds, invert=True).points)
            mask_pts_labelled = np.hstack([mask_without_obj, np.zeros((len(mask_without_obj),1))])

            labelled_pts = np.vstack([mask_pts_labelled, obj_pts_labelled])
            box_pts = np.asarray(pcd_gtboxes['gt_boxes'][gtbox_idx].get_box_points())
            num_points_in_gt = len(cropped_np)
       
        
        # Save pcl
        fname = f"{instance_dataset_id:06}"
        car_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/velodyne')
        car_dir.mkdir(parents=True, exist_ok=True)
        car_fname = str(car_dir / f'{fname}.bin')
        points = np.float32(labelled_pts)
        points.tofile(car_fname)
        
        # Save points labels
        label_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/labels')
        label_dir.mkdir(parents=True, exist_ok=True)
        label_fname = str(label_dir / f'{fname}.label')
        labels = np.uint32(labelled_pts[:,3])
        labels.tofile(label_fname)
        
        # Save gt bboxes
        box_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/gt_bboxes')    
        box_dir.mkdir(parents=True, exist_ok=True)
        np.savetxt(str(box_dir / f'{fname}.txt'), box_pts, delimiter=' ')
        
        # Save img
        img_dir = Path(f'{mesher.data_obj.root_dir}/exported/lidar_seg_data/points_in_{export_tag}/image')    
        img_dir.mkdir(parents=True, exist_ok=True)
        img = mesher.data_obj.get_image(sample_idx, channel="image_2")
        imglabels = inst_labels[object_id]
        ann_img = draw_lidar_on_image([], img, instances=[imglabels], display=False)
        Image.fromarray(ann_img).save(str(img_dir / f'{fname}.png'))

        print(f"car #{instance_dataset_id}: Exported {object_id+1}/{len(i_clouds)} | total pts-{len(labelled_pts)}, gt pts - {num_points_in_gt}")
        instance_dataset_id = instance_dataset_id + 1

car #0: Exported 1/1 | total pts-72, gt pts - 59
car #1: Exported 1/4 | total pts-85, gt pts - 0
car #2: Exported 2/4 | total pts-613, gt pts - 557
car #3: Exported 4/4 | total pts-9, gt pts - 0
car #4: Exported 1/3 | total pts-75, gt pts - 58
car #5: Exported 2/3 | total pts-27, gt pts - 24
car #6: Exported 1/5 | total pts-353, gt pts - 260
car #7: Exported 2/5 | total pts-62, gt pts - 52
car #8: Exported 3/5 | total pts-34, gt pts - 20
car #9: Exported 4/5 | total pts-8, gt pts - 0
car #10: Exported 5/5 | total pts-14, gt pts - 0
car #11: Exported 1/3 | total pts-156, gt pts - 154
car #12: Exported 2/3 | total pts-18, gt pts - 17
car #13: Exported 3/3 | total pts-5, gt pts - 5
car #14: Exported 1/9 | total pts-1388, gt pts - 1098
car #15: Exported 2/9 | total pts-990, gt pts - 738
car #16: Exported 3/9 | total pts-1697, gt pts - 1441
car #17: Exported 4/9 | total pts-661, gt pts - 574
car #18: Exported 5/9 | total pts-200, gt pts - 136
car #19: Exported 6/9 | total pts-46, gt pts - 3

car #161: Exported 6/9 | total pts-75, gt pts - 65
car #162: Exported 7/9 | total pts-10, gt pts - 0
car #163: Exported 8/9 | total pts-10, gt pts - 5
car #164: Exported 9/9 | total pts-7, gt pts - 7
car #165: Exported 1/12 | total pts-601, gt pts - 478
car #166: Exported 2/12 | total pts-435, gt pts - 0
car #167: Exported 3/12 | total pts-911, gt pts - 804
car #168: Exported 4/12 | total pts-451, gt pts - 320
car #169: Exported 5/12 | total pts-78, gt pts - 0
car #170: Exported 6/12 | total pts-453, gt pts - 384
car #171: Exported 7/12 | total pts-256, gt pts - 234
car #172: Exported 8/12 | total pts-194, gt pts - 150
car #173: Exported 9/12 | total pts-196, gt pts - 181
car #174: Exported 10/12 | total pts-39, gt pts - 24
car #175: Exported 11/12 | total pts-114, gt pts - 102
car #176: Exported 12/12 | total pts-51, gt pts - 49
car #177: Exported 1/4 | total pts-483, gt pts - 129
car #178: Exported 2/4 | total pts-1229, gt pts - 950
car #179: Exported 3/4 | total pts-669, gt pts - 57

car #320: Exported 1/2 | total pts-232, gt pts - 169
car #321: Exported 2/2 | total pts-24, gt pts - 0
car #322: Exported 1/8 | total pts-79, gt pts - 0
car #323: Exported 2/8 | total pts-44, gt pts - 0
car #324: Exported 3/8 | total pts-45, gt pts - 42
car #325: Exported 4/8 | total pts-33, gt pts - 0
car #326: Exported 5/8 | total pts-35, gt pts - 0
car #327: Exported 6/8 | total pts-11, gt pts - 0
car #328: Exported 7/8 | total pts-15, gt pts - 0
car #329: Exported 1/5 | total pts-125, gt pts - 88
car #330: Exported 2/5 | total pts-147, gt pts - 129
car #331: Exported 3/5 | total pts-103, gt pts - 93
car #332: Exported 4/5 | total pts-15, gt pts - 10
car #333: Exported 5/5 | total pts-8, gt pts - 0
car #334: Exported 1/12 | total pts-1834, gt pts - 1573
car #335: Exported 2/12 | total pts-615, gt pts - 526
car #336: Exported 3/12 | total pts-362, gt pts - 316
car #337: Exported 4/12 | total pts-328, gt pts - 264
car #338: Exported 5/12 | total pts-30, gt pts - 0
car #339: Exported 6

car #478: Exported 6/11 | total pts-143, gt pts - 127
car #479: Exported 7/11 | total pts-54, gt pts - 0
car #480: Exported 8/11 | total pts-46, gt pts - 0
car #481: Exported 9/11 | total pts-73, gt pts - 69
car #482: Exported 10/11 | total pts-40, gt pts - 27
car #483: Exported 11/11 | total pts-29, gt pts - 0
car #484: Exported 1/3 | total pts-198, gt pts - 0
car #485: Exported 2/3 | total pts-378, gt pts - 326
car #486: Exported 3/3 | total pts-301, gt pts - 215
car #487: Exported 1/12 | total pts-1700, gt pts - 1441
car #488: Exported 2/12 | total pts-812, gt pts - 586
car #489: Exported 3/12 | total pts-425, gt pts - 356
car #490: Exported 4/12 | total pts-99, gt pts - 98
car #491: Exported 5/12 | total pts-125, gt pts - 103
car #492: Exported 6/12 | total pts-162, gt pts - 149
car #493: Exported 7/12 | total pts-69, gt pts - 34
car #494: Exported 8/12 | total pts-69, gt pts - 64
car #495: Exported 9/12 | total pts-33, gt pts - 28
car #496: Exported 10/12 | total pts-27, gt pts - 

car #636: Exported 1/9 | total pts-2241, gt pts - 1870
car #637: Exported 2/9 | total pts-1662, gt pts - 1192
car #638: Exported 3/9 | total pts-239, gt pts - 143
car #639: Exported 4/9 | total pts-242, gt pts - 188
car #640: Exported 5/9 | total pts-208, gt pts - 160
car #641: Exported 6/9 | total pts-21, gt pts - 19
car #642: Exported 7/9 | total pts-14, gt pts - 12
car #643: Exported 1/1 | total pts-72, gt pts - 72
car #644: Exported 1/5 | total pts-816, gt pts - 702
car #645: Exported 2/5 | total pts-230, gt pts - 223
car #646: Exported 3/5 | total pts-33, gt pts - 31
car #647: Exported 4/5 | total pts-11, gt pts - 8
car #648: Exported 1/9 | total pts-193, gt pts - 168
car #649: Exported 2/9 | total pts-13, gt pts - 0
car #650: Exported 3/9 | total pts-23, gt pts - 14
car #651: Exported 4/9 | total pts-47, gt pts - 41
car #652: Exported 5/9 | total pts-7, gt pts - 0
car #653: Exported 7/9 | total pts-21, gt pts - 0
car #654: Exported 8/9 | total pts-13, gt pts - 0
car #655: Exporte

...

car #32946: Exported 4/4 | total pts-12, gt pts - 0
car #32947: Exported 1/13 | total pts-884, gt pts - 792
car #32948: Exported 2/13 | total pts-1004, gt pts - 742
car #32949: Exported 3/13 | total pts-734, gt pts - 675
car #32950: Exported 4/13 | total pts-326, gt pts - 209
car #32951: Exported 5/13 | total pts-381, gt pts - 305
car #32952: Exported 6/13 | total pts-458, gt pts - 406
car #32953: Exported 7/13 | total pts-136, gt pts - 0
car #32954: Exported 8/13 | total pts-285, gt pts - 229
car #32955: Exported 9/13 | total pts-113, gt pts - 110
car #32956: Exported 10/13 | total pts-93, gt pts - 87
car #32957: Exported 11/13 | total pts-67, gt pts - 60
car #32958: Exported 12/13 | total pts-25, gt pts - 0
car #32959: Exported 13/13 | total pts-5, gt pts - 0
car #32960: Exported 1/2 | total pts-932, gt pts - 635
car #32961: Exported 2/2 | total pts-246, gt pts - 208
car #32962: Exported 1/3 | total pts-550, gt pts - 456
car #32963: Exported 2/3 | total pts-1079, gt pts - 900
car #32

car #33098: Exported 5/7 | total pts-70, gt pts - 64
car #33099: Exported 6/7 | total pts-59, gt pts - 56
car #33100: Exported 7/7 | total pts-30, gt pts - 30
car #33101: Exported 1/12 | total pts-192, gt pts - 72
car #33102: Exported 2/12 | total pts-94, gt pts - 85
car #33103: Exported 3/12 | total pts-42, gt pts - 0
car #33104: Exported 4/12 | total pts-5, gt pts - 0
car #33105: Exported 6/12 | total pts-35, gt pts - 24
car #33106: Exported 7/12 | total pts-28, gt pts - 27
car #33107: Exported 8/12 | total pts-8, gt pts - 0
car #33108: Exported 10/12 | total pts-7, gt pts - 0
car #33109: Exported 12/12 | total pts-5, gt pts - 0
car #33110: Exported 1/1 | total pts-529, gt pts - 0
car #33111: Exported 1/4 | total pts-120, gt pts - 119
car #33112: Exported 2/4 | total pts-24, gt pts - 23
car #33113: Exported 3/4 | total pts-27, gt pts - 12
car #33114: Exported 4/4 | total pts-13, gt pts - 10
car #33115: Exported 1/9 | total pts-660, gt pts - 483
car #33116: Exported 2/9 | total pts-33

car #33250: Exported 1/1 | total pts-11, gt pts - 4
car #33251: Exported 1/6 | total pts-903, gt pts - 802
car #33252: Exported 2/6 | total pts-331, gt pts - 313
car #33253: Exported 3/6 | total pts-149, gt pts - 135
car #33254: Exported 4/6 | total pts-31, gt pts - 28
car #33255: Exported 6/6 | total pts-7, gt pts - 0
car #33256: Exported 1/4 | total pts-423, gt pts - 366
car #33257: Exported 2/4 | total pts-13, gt pts - 0
car #33258: Exported 3/4 | total pts-7, gt pts - 0
car #33259: Exported 1/12 | total pts-813, gt pts - 672
car #33260: Exported 2/12 | total pts-339, gt pts - 285
car #33261: Exported 3/12 | total pts-185, gt pts - 163
car #33262: Exported 4/12 | total pts-113, gt pts - 104
car #33263: Exported 5/12 | total pts-69, gt pts - 0
car #33264: Exported 6/12 | total pts-25, gt pts - 8
car #33265: Exported 7/12 | total pts-46, gt pts - 13
car #33266: Exported 8/12 | total pts-19, gt pts - 0
car #33267: Exported 9/12 | total pts-49, gt pts - 42
car #33268: Exported 10/12 | t

car #33402: Exported 1/4 | total pts-24, gt pts - 21
car #33403: Exported 2/4 | total pts-39, gt pts - 29
car #33404: Exported 3/4 | total pts-16, gt pts - 13
car #33405: Exported 4/4 | total pts-7, gt pts - 5
car #33406: Exported 1/3 | total pts-105, gt pts - 88
car #33407: Exported 2/3 | total pts-32, gt pts - 25
car #33408: Exported 3/3 | total pts-12, gt pts - 6
car #33409: Exported 1/10 | total pts-564, gt pts - 194
car #33410: Exported 2/10 | total pts-1208, gt pts - 904
car #33411: Exported 3/10 | total pts-925, gt pts - 641
car #33412: Exported 4/10 | total pts-374, gt pts - 313
car #33413: Exported 5/10 | total pts-334, gt pts - 278
car #33414: Exported 6/10 | total pts-140, gt pts - 1
car #33415: Exported 7/10 | total pts-110, gt pts - 81
car #33416: Exported 8/10 | total pts-43, gt pts - 37
car #33417: Exported 9/10 | total pts-15, gt pts - 14
car #33418: Exported 10/10 | total pts-5, gt pts - 0
car #33419: Exported 1/1 | total pts-26, gt pts - 17
car #33420: Exported 1/5 | 

car #33554: Exported 9/12 | total pts-24, gt pts - 22
car #33555: Exported 10/12 | total pts-17, gt pts - 8
car #33556: Exported 11/12 | total pts-15, gt pts - 14
car #33557: Exported 12/12 | total pts-6, gt pts - 0
car #33558: Exported 1/7 | total pts-1010, gt pts - 886
car #33559: Exported 2/7 | total pts-507, gt pts - 465
car #33560: Exported 3/7 | total pts-196, gt pts - 171
car #33561: Exported 4/7 | total pts-286, gt pts - 241
car #33562: Exported 5/7 | total pts-53, gt pts - 45
car #33563: Exported 6/7 | total pts-22, gt pts - 20
car #33564: Exported 1/1 | total pts-1656, gt pts - 1490
car #33565: Exported 1/7 | total pts-1603, gt pts - 1334
car #33566: Exported 2/7 | total pts-1249, gt pts - 1176
car #33567: Exported 3/7 | total pts-324, gt pts - 309
car #33568: Exported 4/7 | total pts-551, gt pts - 507
car #33569: Exported 5/7 | total pts-252, gt pts - 237
car #33570: Exported 6/7 | total pts-70, gt pts - 67
car #33571: Exported 7/7 | total pts-47, gt pts - 38
car #33572: Exp